In [1]:
latest_gameweek = 6

In [2]:
import pandas as pd
import numpy as np
from pathlib import Path
from pulp import LpMaximize, LpProblem, LpStatus, lpSum, LpVariable

# Solver

In [3]:
def optimize(df, max_price, expected_column, captain_double_points=True):
    '''Function for solving the optimization problem.'''    
    # PRELIMINARIES

    # Create the model
    model = LpProblem(name="FPL", sense=LpMaximize)    
    variables = [LpVariable(name=f'{ix}', cat='Binary') for ix in df.index]
    captaincy_variables = [LpVariable(name=f'cap_{ix}', cat='Binary') for ix in df.index]
    prices = [df.loc[ix,'price'] for ix in df.index]
    # measure of player quality
    expected_points = [df.loc[ix,expected_column] for ix in df.index]
    goalkeepers = [1.0 if df.loc[ix,'position']=='GK' else 0.0 for ix in df.index]
    defenders = [1.0 if df.loc[ix,'position']=='DEF' else 0.0 for ix in df.index]
    midfielders = [1.0 if df.loc[ix,'position']=='MID' else 0.0 for ix in df.index]
    forwards = [1.0 if df.loc[ix,'position']=='FWD' else 0.0 for ix in df.index]
    teams = []
    for team in df['team'].unique():
        teams.append( [1.0 if df.loc[ix,'team']==team else 0.0 for ix in df.index] )

    # CONSTRAINTS

    # select 11 players
    model += lpSum(variables) == 11
    # select 1 captain
    model += lpSum(captaincy_variables) == 1
    # captain must be one of the 11 players in the team
    for i in range(0,len(variables)):
        model += captaincy_variables[i] <= variables[i]
    # set maximum price for starting 11
    model += np.dot(prices,variables) <= max_price
    # only 1 goalkeeper
    model += np.dot(goalkeepers,variables) == 1
    # at least 3 defenders
    model += np.dot(defenders,variables) >= 3
    # at most 5 defenders
    model += np.dot(defenders,variables) <= 5
    # at most 5 midfielders
    model += np.dot(midfielders,variables) <= 5
    # at least 1 forward
    model += np.dot(forwards,variables) >= 1
    # at most 3 forwards
    model += np.dot(forwards,variables) <= 3
    # max 3 players from any given team
    for team in teams:
        model += np.dot(team,variables) <= 3

    # OBJECTIVE
    if captain_double_points:
        # the second part doubles the captain's points
        model += np.dot(expected_points,variables) + np.dot(expected_points,captaincy_variables)
    else:
        model += np.dot(expected_points,variables)

    # SOLVE OPTIMIZATION

    status = model.solve()
    print(f'Status: {LpStatus[model.status]}')
    #print(f'Mean total points per gameweek: {model.objective.value()}')

    players = [str(var) for var in model.variables() if var.value()==1]
    captain = [player for player in players if 'cap' in player]
    captain = int(captain[0].replace('cap_', ''))
    players = [int(player) for player in players if 'cap' not in player]
    dream_team = df.loc[players]
    cost = (dream_team['price']).sum()
    exp_points = dream_team[expected_column].sum() + df.loc[captain, expected_column]
    print(f'Cost: {cost}')
    print(f'Expected points per week: {exp_points}')
    
    display(dream_team[['position','name', 'team', 'price', expected_column]].sort_values('position'))
    
    return players

# Data

In [4]:
path = Path(f'../data/predictions/gameweek{latest_gameweek}.csv')
projections = pd.read_csv(path, index_col=0)
projections.head(5)

name  element_type  home  corners_and_indirect_freekicks_order  \
0  Aaron Hickey             2     0                                   NaN   
1  Aaron Hickey             2     0                                   NaN   
2  Aaron Hickey             2     1                                   NaN   
3  Aaron Hickey             2     0                                   NaN   
4  Aaron Hickey             2     1                                   NaN   

   creativity_rank  direct_freekicks_order  ict_index_rank  influence_rank  \
0              233                     NaN             241             221   
1              233                     NaN             241             221   
2              233                     NaN             241             221   
3              233                     NaN             241             221   
4              233                     NaN             241             221   

   minutes  now_cost  ...  gameweek_xG_expanding_per90  \
0      472        45  ...                     0.031009   
1      472        45  ...                     0.031009   
2      472        45  ...                     0.031009   
3      472        45  ...                     0.031009   
4      472        45  ...                     0.031009   

   gameweek_xA_expanding_per90  gameweek_xGA_expanding_per90  \
0                     0.024364                      1.268417   
1                     0.024364                      1.268417   
2                     0.024364                      1.268417   
3                     0.024364                      1.268417   
4                     0.024364                      1.268417   

   gameweek_xPoints_expanding_per90  xG_overperformance  team_name  \
0                          3.358311                 0.0  Brentford   
1                          3.358311                 0.0  Brentford   
2                          3.358311                 0.0  Brentford   
3                          3.358311                 0.0  Brentford   
4                          3.358311                 0.0  Brentford   

       opponent_team                  date  gameweek  expected_points  
0  Nottingham Forest  2023-10-01T13:00:00Z         7         2.800363  
1     Manchester Utd  2023-10-07T14:00:00Z         8         2.099588  
2            Burnley  2023-10-21T14:00:00Z         9         2.818016  
3            Chelsea  2023-10-28T11:30:00Z        10         2.177998  
4           West Ham  2023-11-04T15:00:00Z        11         2.560032  

[5 rows x 113 columns]

In [5]:
# decay for future projected points to model uncertainty increasing over time
decay_coeff = 0.875
projections['expected_points_with_decay'] = ( projections['expected_points']*decay_coeff
                                              **(projections['gameweek']-1) )
projections.head(5)

name  element_type  home  corners_and_indirect_freekicks_order  \
0  Aaron Hickey             2     0                                   NaN   
1  Aaron Hickey             2     0                                   NaN   
2  Aaron Hickey             2     1                                   NaN   
3  Aaron Hickey             2     0                                   NaN   
4  Aaron Hickey             2     1                                   NaN   

   creativity_rank  direct_freekicks_order  ict_index_rank  influence_rank  \
0              233                     NaN             241             221   
1              233                     NaN             241             221   
2              233                     NaN             241             221   
3              233                     NaN             241             221   
4              233                     NaN             241             221   

   minutes  now_cost  ...  gameweek_xA_expanding_per90  \
0      472        45  ...                     0.024364   
1      472        45  ...                     0.024364   
2      472        45  ...                     0.024364   
3      472        45  ...                     0.024364   
4      472        45  ...                     0.024364   

   gameweek_xGA_expanding_per90  gameweek_xPoints_expanding_per90  \
0                      1.268417                          3.358311   
1                      1.268417                          3.358311   
2                      1.268417                          3.358311   
3                      1.268417                          3.358311   
4                      1.268417                          3.358311   

   xG_overperformance  team_name      opponent_team                  date  \
0                 0.0  Brentford  Nottingham Forest  2023-10-01T13:00:00Z   
1                 0.0  Brentford     Manchester Utd  2023-10-07T14:00:00Z   
2                 0.0  Brentford            Burnley  2023-10-21T14:00:00Z   
3                 0.0  Brentford            Chelsea  2023-10-28T11:30:00Z   
4                 0.0  Brentford           West Ham  2023-11-04T15:00:00Z   

   gameweek  expected_points  expected_points_with_decay  
0         7         2.800363                    1.256790  
1         8         2.099588                    0.824499  
2         9         2.818016                    0.968295  
3        10         2.177998                    0.654832  
4        11         2.560032                    0.673482  

[5 rows x 114 columns]

In [6]:
my_gameweeks = np.arange(latest_gameweek+1, latest_gameweek+11, 1)
#my_gameweeks = np.arange(latest_gameweek+1, latest_gameweek+4, 1)
#my_gameweeks = np.arange(latest_gameweek+2, latest_gameweek+12, 1)
df = projections[projections['gameweek'].isin(my_gameweeks)].groupby(by=['name', 'team_name']).sum()\
                                                        [['expected_points','expected_points_with_decay']]
df['number_of_games'] = (
    projections[projections['gameweek']
    .isin(my_gameweeks)]
    .groupby(['name', 'team_name'])
    .count()['element_type']
)

df = df.reset_index()

df['position'] = [projections.loc[projections['name']==name, 'element_type'].values[0] for name in df['name']]
position_dict={1:'GK', 2:'DEF', 3:'MID', 4:'FWD'}
df['position'] = df['position'].map(position_dict)
df['position'] = pd.Categorical(df['position'], ['GK','DEF','MID','FWD'])

df['price'] = [projections.loc[projections['name']==name, 'now_cost'].values[0] for name in df['name']]
df['price'] = df['price'] / 10.0

df['team'] = [projections.loc[projections['name']==name, 'team_name'].values[0] for name in df['name']]

df

name       team_name  expected_points  \
0                Aaron Hickey       Brentford        24.680199   
1              Aaron Ramsdale         Arsenal        36.713062   
2                Aaron Ramsey         Burnley        26.330710   
3           Aaron Wan-Bissaka  Manchester Utd        30.634670   
4          Abdoulaye Doucouré         Everton        37.231485   
..                        ...             ...              ...   
419               Yoane Wissa       Brentford        37.846445   
420           Youri Tielemans     Aston Villa        24.393393   
421  Youssef Ramalho Chermiti         Everton         9.579638   
422             Yves Bissouma       Tottenham        26.526422   
423              Zeki Amdouni         Burnley        28.086314   

     expected_points_with_decay  number_of_games position  price  \
0                      6.510284               10      DEF    4.5   
1                      9.635422               10       GK    5.0   
2                      7.292007               11      MID    5.0   
3                      8.201161               10      DEF    4.6   
4                      9.911588               10      MID    5.5   
..                          ...              ...      ...    ...   
419                    9.978754               10      FWD    6.0   
420                    6.545915               10      MID    5.7   
421                    2.579863               10      FWD    4.9   
422                    7.059345               10      MID    5.0   
423                    7.763076               11      FWD    5.4   

               team  
0         Brentford  
1           Arsenal  
2           Burnley  
3    Manchester Utd  
4           Everton  
..              ...  
419       Brentford  
420     Aston Villa  
421         Everton  
422       Tottenham  
423         Burnley  

[424 rows x 8 columns]

# Optimization

In [7]:
team_value = 99.6
money_in_the_bank = 0.9
allowed_bench_value = 17.5
max_price = team_value + money_in_the_bank - allowed_bench_value

In [8]:
ban = []

# ban some cheap keepers in good teams who don't actually play
cheap_keepers = []
cheap_keepers_ix = df[df['name'].isin(cheap_keepers)].index
ban = ban + list(cheap_keepers_ix)

# ban given outfield players
ban_field = ['Kevin De Bruyne']
ban_field_ix = df[df['name'].isin(ban_field)].index
ban = ban + list(ban_field_ix)

my_df = df.drop(ban).copy()

In [9]:
players = optimize(my_df, max_price, 'expected_points_with_decay')

Welcome to the CBC MILP Solver 
Version: 2.10.3 
Build Date: Dec 15 2019 

command line - /Users/jaakkotoivonen/Documents/my_stuff/Fantasy-Premier-League/venv23-24/lib/python3.10/site-packages/pulp/solverdir/cbc/osx/64/cbc /var/folders/ml/jr8p__z97xx1jjb90rwg7hfm0000gn/T/1747a63e06634ba4bf5529bb30352d41-pulp.mps max timeMode elapsed branch printingOptions all solution /var/folders/ml/jr8p__z97xx1jjb90rwg7hfm0000gn/T/1747a63e06634ba4bf5529bb30352d41-pulp.sol (default strategy 1)
At line 2 NAME          MODEL
At line 3 ROWS
At line 457 COLUMNS
At line 6158 RHS
At line 6611 BOUNDS
At line 7458 ENDATA
Problem MODEL has 452 rows, 846 columns and 3162 elements
Coin0008I MODEL read with 0 errors
Option for timeMode changed from cpu to elapsed
Continuous objective value is 160.222 - 0.00 seconds
Cgl0004I processed model has 450 rows, 846 columns (846 integer (846 of which binary)) and 2961 elements
Cbc0038I Initial state - 2 integers unsatisfied sum - 0.83871
Cbc0038I Pass   1: suminf.    0.49

position                    name             team  price  \
16        GK         Alphonse Areola         West Ham    4.2   
23       DEF        Andrew Robertson        Liverpool    6.6   
231      DEF         Kieran Trippier    Newcastle Utd    6.6   
400      DEF  Trent Alexander-Arnold        Liverpool    7.9   
174      MID          James Maddison        Tottenham    7.9   
184      MID            Jarrod Bowen         West Ham    7.1   
225      MID            Kaoru Mitoma         Brighton    6.6   
296      MID           Mohamed Salah        Liverpool   12.5   
61       MID             Bukayo Saka          Arsenal    8.7   
218      FWD          Julián Álvarez  Manchester City    7.0   
325      FWD           Ollie Watkins      Aston Villa    7.9   

     expected_points_with_decay  
16                     9.587655  
23                    12.339600  
231                   11.850392  
400                   12.779027  
174                   13.431332  
184                   14.188331  
225                   12.557580  
296                   16.566857  
61                    15.130709  
218                   12.458734  
325                   12.606532

In [10]:
sigma=0.5
simulation_rounds = 500
next_gameweek=latest_gameweek+1

ban = []

# ban some cheap keepers in good teams who don't actually play
cheap_keepers = []
cheap_keepers_ix = df[df['name'].isin(cheap_keepers)].index
ban = ban + list(cheap_keepers_ix)

# ban given outfield players
ban_field = ['Kevin De Bruyne']
ban_field_ix = df[df['name'].isin(ban_field)].index
ban = ban + list(ban_field_ix)

results = []
for i in range(simulation_rounds):
 
    # add random noise to expected points (a fixed offset for every projection of any given player)
    projections['expected_points_with_noise'] = (projections
    .groupby('name')
    .apply(lambda x: x['expected_points']+np.random.normal(0,sigma))
    .reset_index()
    .sort_values('level_1')
    ['expected_points']
    .values
    )

    # decay
    projections['expected_points_with_noise_with_decay'] = ( projections['expected_points_with_noise']*decay_coeff
                                              **(projections['gameweek']-next_gameweek) )

    df['expected_points_with_noise_with_decay'] = projections[projections['gameweek'].isin(my_gameweeks)].groupby(by=['name', 'team_name']).sum()\
                                                            ['expected_points_with_noise_with_decay'].values

    my_df = df.drop(ban).copy()
    
    players = optimize(my_df, max_price, 'expected_points_with_noise_with_decay')

    results.append(players)
    

Welcome to the CBC MILP Solver 
Version: 2.10.3 
Build Date: Dec 15 2019 

command line - /Users/jaakkotoivonen/Documents/my_stuff/Fantasy-Premier-League/venv23-24/lib/python3.10/site-packages/pulp/solverdir/cbc/osx/64/cbc /var/folders/ml/jr8p__z97xx1jjb90rwg7hfm0000gn/T/ea5eea7f5c064bcb9e87c5997ddb37b8-pulp.mps max timeMode elapsed branch printingOptions all solution /var/folders/ml/jr8p__z97xx1jjb90rwg7hfm0000gn/T/ea5eea7f5c064bcb9e87c5997ddb37b8-pulp.sol (default strategy 1)
At line 2 NAME          MODEL
At line 3 ROWS
At line 457 COLUMNS
At line 6158 RHS
At line 6611 BOUNDS
At line 7458 ENDATA
Problem MODEL has 452 rows, 846 columns and 3162 elements
Coin0008I MODEL read with 0 errors
Option for timeMode changed from cpu to elapsed
Continuous objective value is 385.178 - 0.00 seconds
Cgl0004I processed model has 450 rows, 846 columns (846 integer (846 of which binary)) and 2961 elements
Cbc0038I Initial state - 2 integers unsatisfied sum - 0.0322581
Cbc0038I Solution found of -385.

position                    name             team  price  \
16        GK         Alphonse Areola         West Ham    4.2   
23       DEF        Andrew Robertson        Liverpool    6.6   
333      DEF              Pau Torres      Aston Villa    4.5   
400      DEF  Trent Alexander-Arnold        Liverpool    7.9   
149      MID           Heung-Min Son        Tottenham    9.2   
174      MID          James Maddison        Tottenham    7.9   
184      MID            Jarrod Bowen         West Ham    7.1   
332      MID             Pascal Groß         Brighton    6.3   
61       MID             Bukayo Saka          Arsenal    8.7   
108      FWD         Dominic Solanke      Bournemouth    6.4   
123      FWD          Erling Haaland  Manchester City   14.1   

     expected_points_with_noise_with_decay  
16                               26.073171  
23                               30.717739  
333                              28.935449  
400                              32.751564  
149                              32.145905  
174                              34.359127  
184                              37.798143  
332                              29.486405  
61                               33.298085  
108                              27.849701  
123                              33.932547

Welcome to the CBC MILP Solver 
Version: 2.10.3 
Build Date: Dec 15 2019 

command line - /Users/jaakkotoivonen/Documents/my_stuff/Fantasy-Premier-League/venv23-24/lib/python3.10/site-packages/pulp/solverdir/cbc/osx/64/cbc /var/folders/ml/jr8p__z97xx1jjb90rwg7hfm0000gn/T/27ca7e54e3e645669a7d3c4048d695d1-pulp.mps max timeMode elapsed branch printingOptions all solution /var/folders/ml/jr8p__z97xx1jjb90rwg7hfm0000gn/T/27ca7e54e3e645669a7d3c4048d695d1-pulp.sol (default strategy 1)
At line 2 NAME          MODEL
At line 3 ROWS
At line 457 COLUMNS
At line 6158 RHS
At line 6611 BOUNDS
At line 7458 ENDATA
Problem MODEL has 452 rows, 846 columns and 3162 elements
Coin0008I MODEL read with 0 errors
Option for timeMode changed from cpu to elapsed
Continuous objective value is 381.437 - 0.00 seconds
Cgl0004I processed model has 450 rows, 846 columns (846 integer (846 of which binary)) and 2961 elements
Cbc0038I Initial state - 2 integers unsatisfied sum - 0.285714
Cbc0038I Solution found of -381.2

position                    name             team  price  \
388       GK         Thomas Kaminski            Luton    4.5   
231      DEF         Kieran Trippier    Newcastle Utd    6.6   
335      DEF             Pedro Porro        Tottenham    5.0   
400      DEF  Trent Alexander-Arnold        Liverpool    7.9   
149      MID           Heung-Min Son        Tottenham    9.2   
184      MID            Jarrod Bowen         West Ham    7.1   
296      MID           Mohamed Salah        Liverpool   12.5   
338      MID              Phil Foden  Manchester City    7.6   
58       MID  Bruno Borges Fernandes   Manchester Utd    8.4   
64       FWD           Callum Wilson    Newcastle Utd    7.8   
70       FWD          Carlton Morris            Luton    5.5   

     expected_points_with_noise_with_decay  
388                              24.323029  
231                              28.697514  
335                              29.438582  
400                              30.423972  
149                              36.747630  
184                              32.739286  
296                              36.934083  
338                              31.098553  
58                               31.851973  
64                               30.987747  
70                               31.038893

Welcome to the CBC MILP Solver 
Version: 2.10.3 
Build Date: Dec 15 2019 

command line - /Users/jaakkotoivonen/Documents/my_stuff/Fantasy-Premier-League/venv23-24/lib/python3.10/site-packages/pulp/solverdir/cbc/osx/64/cbc /var/folders/ml/jr8p__z97xx1jjb90rwg7hfm0000gn/T/c2a29aba60a349f5b69574bf3d59ddb6-pulp.mps max timeMode elapsed branch printingOptions all solution /var/folders/ml/jr8p__z97xx1jjb90rwg7hfm0000gn/T/c2a29aba60a349f5b69574bf3d59ddb6-pulp.sol (default strategy 1)
At line 2 NAME          MODEL
At line 3 ROWS
At line 457 COLUMNS
At line 6158 RHS
At line 6611 BOUNDS
At line 7458 ENDATA
Problem MODEL has 452 rows, 846 columns and 3162 elements
Coin0008I MODEL read with 0 errors
Option for timeMode changed from cpu to elapsed
Continuous objective value is 377.042 - 0.00 seconds
Cgl0004I processed model has 450 rows, 846 columns (846 integer (846 of which binary)) and 2961 elements
Cbc0038I Initial state - 2 integers unsatisfied sum - 0.677419
Cbc0038I Solution found of -375.4

...

position                    name             team  price  \
311       GK               Nick Pope    Newcastle Utd    5.5   
194      DEF        Joachim Andersen   Crystal Palace    4.7   
23       DEF        Andrew Robertson        Liverpool    6.6   
400      DEF  Trent Alexander-Arnold        Liverpool    7.9   
149      MID           Heung-Min Son        Tottenham    9.2   
180      MID       James Ward-Prowse         West Ham    6.3   
225      MID            Kaoru Mitoma         Brighton    6.6   
296      MID           Mohamed Salah        Liverpool   12.5   
61       MID             Bukayo Saka          Arsenal    8.7   
218      FWD          Julián Álvarez  Manchester City    7.0   
64       FWD           Callum Wilson    Newcastle Utd    7.8   

     expected_points_with_noise_with_decay  
311                              27.743433  
194                              27.512583  
23                               28.244216  
400                              28.543382  
149                              33.902463  
180                              32.814125  
225                              32.459909  
296                              35.577028  
61                               36.883531  
218                              31.036158  
64                               28.901848

Welcome to the CBC MILP Solver 
Version: 2.10.3 
Build Date: Dec 15 2019 

command line - /Users/jaakkotoivonen/Documents/my_stuff/Fantasy-Premier-League/venv23-24/lib/python3.10/site-packages/pulp/solverdir/cbc/osx/64/cbc /var/folders/ml/jr8p__z97xx1jjb90rwg7hfm0000gn/T/cee80e514d754a0ebef1670614a978f4-pulp.mps max timeMode elapsed branch printingOptions all solution /var/folders/ml/jr8p__z97xx1jjb90rwg7hfm0000gn/T/cee80e514d754a0ebef1670614a978f4-pulp.sol (default strategy 1)
At line 2 NAME          MODEL
At line 3 ROWS
At line 457 COLUMNS
At line 6158 RHS
At line 6611 BOUNDS
At line 7458 ENDATA
Problem MODEL has 452 rows, 846 columns and 3162 elements
Coin0008I MODEL read with 0 errors
Option for timeMode changed from cpu to elapsed
Continuous objective value is 386.774 - 0.00 seconds
Cgl0004I processed model has 450 rows, 846 columns (846 integer (846 of which binary)) and 2961 elements
Cbc0038I Initial state - 2 integers unsatisfied sum - 0.930233
Cbc0038I Solution found of -383.9

position              name             team  price  \
51        GK        Bernd Leno           Fulham    4.7   
23       DEF  Andrew Robertson        Liverpool    6.6   
282      DEF        Matty Cash      Aston Villa    4.8   
380      DEF       Sven Botman    Newcastle Utd    4.7   
184      MID      Jarrod Bowen         West Ham    7.1   
296      MID     Mohamed Salah        Liverpool   12.5   
332      MID       Pascal Groß         Brighton    6.3   
61       MID       Bukayo Saka          Arsenal    8.7   
123      FWD    Erling Haaland  Manchester City   14.1   
218      FWD    Julián Álvarez  Manchester City    7.0   
70       FWD    Carlton Morris            Luton    5.5   

     expected_points_with_noise_with_decay  
51                               26.197476  
23                               29.364823  
282                              29.449657  
380                              25.773598  
184                              32.369335  
296                              40.458444  
332                              33.711712  
61                               31.674929  
123                              34.276609  
218                              32.964973  
70                               28.199517

Welcome to the CBC MILP Solver 
Version: 2.10.3 
Build Date: Dec 15 2019 

command line - /Users/jaakkotoivonen/Documents/my_stuff/Fantasy-Premier-League/venv23-24/lib/python3.10/site-packages/pulp/solverdir/cbc/osx/64/cbc /var/folders/ml/jr8p__z97xx1jjb90rwg7hfm0000gn/T/54a6d09a26414d119aa18d3bea4bc1c9-pulp.mps max timeMode elapsed branch printingOptions all solution /var/folders/ml/jr8p__z97xx1jjb90rwg7hfm0000gn/T/54a6d09a26414d119aa18d3bea4bc1c9-pulp.sol (default strategy 1)
At line 2 NAME          MODEL
At line 3 ROWS
At line 457 COLUMNS
At line 6158 RHS
At line 6611 BOUNDS
At line 7458 ENDATA
Problem MODEL has 452 rows, 846 columns and 3162 elements
Coin0008I MODEL read with 0 errors
Option for timeMode changed from cpu to elapsed
Continuous objective value is 384.482 - 0.00 seconds
Cgl0004I processed model has 450 rows, 846 columns (846 integer (846 of which binary)) and 2961 elements
Cbc0038I Initial state - 2 integers unsatisfied sum - 0.125
Cbc0038I Pass   1: suminf.    0.0377

position                      name             team  price  \
179       GK            James Trafford          Burnley    4.5   
23       DEF          Andrew Robertson        Liverpool    6.6   
385      DEF  Thiago Emiliano da Silva          Chelsea    5.0   
400      DEF    Trent Alexander-Arnold        Liverpool    7.9   
149      MID             Heung-Min Son        Tottenham    9.2   
180      MID         James Ward-Prowse         West Ham    6.3   
184      MID              Jarrod Bowen         West Ham    7.1   
296      MID             Mohamed Salah        Liverpool   12.5   
61       MID               Bukayo Saka          Arsenal    8.7   
218      FWD            Julián Álvarez  Manchester City    7.0   
64       FWD             Callum Wilson    Newcastle Utd    7.8   

     expected_points_with_noise_with_decay  
179                              26.739591  
23                               27.680810  
385                              25.900940  
400                              34.675149  
149                              32.528684  
180                              30.662219  
184                              35.427714  
296                              38.288002  
61                               31.930886  
218                              30.584351  
64                               31.183403

In [11]:
my_df['dream_team_appearances'] = [sum(team.count(player_id) / simulation_rounds for team in results) for player_id in my_df.index]

In [12]:
print('Most appearances, all players:')
display(my_df
        .drop(['team', 'expected_points_with_noise_with_decay'], axis=1)
        .sort_values(by='dream_team_appearances', ascending=False)
        .head(20))

Most appearances, all players:


name        team_name  expected_points  \
296           Mohamed Salah        Liverpool        63.611433   
61              Bukayo Saka          Arsenal        57.479137   
184            Jarrod Bowen         West Ham        52.990589   
400  Trent Alexander-Arnold        Liverpool        49.238596   
23         Andrew Robertson        Liverpool        47.644765   
149           Heung-Min Son        Tottenham        55.067800   
231         Kieran Trippier    Newcastle Utd        44.108987   
218          Julián Álvarez  Manchester City        46.779691   
174          James Maddison        Tottenham        50.755953   
325           Ollie Watkins      Aston Villa        46.908045   
123          Erling Haaland  Manchester City        55.146449   
225            Kaoru Mitoma         Brighton        48.351994   
64            Callum Wilson    Newcastle Utd        44.534145   
180       James Ward-Prowse         West Ham        46.111755   
58   Bruno Borges Fernandes   Manchester Utd        48.202344   
332             Pascal Groß         Brighton        46.968736   
282              Matty Cash      Aston Villa        38.172134   
70           Carlton Morris            Luton        37.187828   
337        Pervis Estupiñán         Brighton        39.716342   
60             Bryan Mbeumo        Brentford        46.722017   

     expected_points_with_decay  number_of_games position  price  \
296                   16.566857               10      MID   12.5   
61                    15.130709               10      MID    8.7   
184                   14.188331               10      MID    7.1   
400                   12.779027               10      DEF    7.9   
23                    12.339600               10      DEF    6.6   
149                   14.578781               10      MID    9.2   
231                   11.850392               10      DEF    6.6   
218                   12.458734               10      FWD    7.0   
174                   13.431332               10      MID    7.9   
325                   12.606532               10      FWD    7.9   
123                   14.709075               10      FWD   14.1   
225                   12.557580               10      MID    6.6   
64                    11.925205               10      FWD    7.8   
180                   12.259567               10      MID    6.3   
58                    12.864694               10      MID    8.4   
332                   12.130946               10      MID    6.3   
282                   10.248519               10      DEF    4.8   
70                    10.735154               11      FWD    5.5   
337                   10.252382               10      DEF    5.3   
60                    12.255409               10      MID    6.9   

     dream_team_appearances  
296                   0.854  
61                    0.786  
184                   0.672  
400                   0.638  
23                    0.570  
149                   0.550  
231                   0.452  
218                   0.430  
174                   0.428  
325                   0.414  
123                   0.326  
225                   0.286  
64                    0.254  
180                   0.218  
58                    0.182  
332                   0.180  
282                   0.164  
70                    0.154  
337                   0.150  
60                    0.148

In [13]:
print('GOALKEEPERS')
display(my_df
        .drop(['team', 'expected_points_with_noise_with_decay'], axis=1)
        [my_df['position']=='GK']
        .sort_values(by='dream_team_appearances', ascending=False)
        .head(20))

GOALKEEPERS


name          team_name  expected_points  \
16             Alphonse Areola           West Ham        36.085188   
311                  Nick Pope      Newcastle Utd        37.479764   
114  Ederson Santana de Moraes    Manchester City        38.084825   
98           David Raya Martin            Arsenal        36.800453   
1               Aaron Ramsdale            Arsenal        36.713062   
15       Alisson Ramses Becker          Liverpool        38.586206   
139          Guglielmo Vicario          Tottenham        34.972888   
363              Sam Johnstone     Crystal Palace        34.206643   
179             James Trafford            Burnley        32.156974   
185               Jason Steele           Brighton        35.221684   
51                  Bernd Leno             Fulham        34.613918   
353             Robert Sánchez            Chelsea        33.493062   
354                Robin Olsen        Aston Villa        32.970464   
24                 André Onana     Manchester Utd        34.327695   
388            Thomas Kaminski              Luton        28.767925   
317       Norberto Murara Neto        Bournemouth        33.155096   
269               Mark Flekken          Brentford        31.533039   
211        José Malheiro de Sá             Wolves        32.711125   
206            Jordan Pickford            Everton        30.073025   
281                Matt Turner  Nottingham Forest        30.365329   

     expected_points_with_decay  number_of_games position  price  \
16                     9.587655               10       GK    4.2   
311                   10.124067               10       GK    5.5   
114                   10.203592               10       GK    5.6   
98                     9.654262               10       GK    4.8   
1                      9.635422               10       GK    5.0   
15                     9.952028               10       GK    5.5   
139                    9.333179               10       GK    5.1   
363                    8.970808               10       GK    4.5   
179                    8.860222               11       GK    4.5   
185                    9.038296               10       GK    4.4   
51                     9.144280               10       GK    4.7   
353                    9.122366               10       GK    4.6   
354                    8.838786               10       GK    4.0   
24                     9.189485               10       GK    4.9   
388                    8.307534               11       GK    4.5   
317                    8.832274               10       GK    4.5   
269                    8.357216               10       GK    4.5   
211                    8.412020               10       GK    5.0   
206                    8.054850               10       GK    4.4   
281                    7.910552               10       GK    4.0   

     dream_team_appearances  
16                    0.126  
311                   0.118  
114                   0.118  
98                    0.078  
1                     0.070  
15                    0.062  
139                   0.050  
363                   0.046  
179                   0.042  
185                   0.042  
51                    0.042  
353                   0.040  
354                   0.036  
24                    0.032  
388                   0.026  
317                   0.024  
269                   0.014  
211                   0.012  
206                   0.006  
281                   0.006

In [14]:
print('DEFENDERS')
display(my_df
        .drop(['team', 'expected_points_with_noise_with_decay'], axis=1)
        [my_df['position']=='DEF']
        .sort_values(by='dream_team_appearances', ascending=False)
        .head(20))

DEFENDERS


name        team_name  expected_points  \
400  Trent Alexander-Arnold        Liverpool        49.238596   
23         Andrew Robertson        Liverpool        47.644765   
231         Kieran Trippier    Newcastle Utd        44.108987   
282              Matty Cash      Aston Villa        38.172134   
337        Pervis Estupiñán         Brighton        39.716342   
254               Luke Shaw   Manchester Utd        38.596016   
380             Sven Botman    Newcastle Utd        36.356276   
257      Mads Juel Andersen            Luton        31.640070   
362   Rúben Gato Alves Dias  Manchester City        37.055645   
73           Charlie Taylor          Burnley        32.383986   
90                 Dan Burn    Newcastle Utd        34.121355   
127            Fabian Schär    Newcastle Utd        34.318418   
415          William Saliba          Arsenal        35.914036   
375         Sergio Reguilón   Manchester Utd        34.003403   
335             Pedro Porro        Tottenham        34.541041   
216          Joško Gvardiol  Manchester City        34.935134   
235             Kyle Walker  Manchester City        34.935268   
43             Ben Chilwell          Chelsea        33.449832   
49           Benjamin White          Arsenal        35.426683   
264              Marc Guéhi   Crystal Palace        33.545316   

     expected_points_with_decay  number_of_games position  price  \
400                   12.779027               10      DEF    7.9   
23                    12.339600               10      DEF    6.6   
231                   11.850392               10      DEF    6.6   
282                   10.248519               10      DEF    4.8   
337                   10.252382               10      DEF    5.3   
254                   10.333251               10      DEF    5.5   
380                    9.820144               10      DEF    4.7   
257                    9.104017               11      DEF    4.0   
362                    9.906979               10      DEF    5.5   
73                     8.908206               11      DEF    3.9   
90                     9.236171               10      DEF    4.5   
127                    9.293198               10      DEF    5.0   
415                    9.418530               10      DEF    5.2   
375                    9.101886               10      DEF    4.4   
335                    9.217290               10      DEF    5.0   
216                    9.347810               10      DEF    5.1   
235                    9.342724               10      DEF    5.3   
43                     9.105767               10      DEF    5.6   
49                     9.294937               10      DEF    5.5   
264                    8.802649               10      DEF    4.5   

     dream_team_appearances  
400                   0.638  
23                    0.570  
231                   0.452  
282                   0.164  
337                   0.150  
254                   0.134  
380                   0.094  
257                   0.072  
362                   0.066  
73                    0.058  
90                    0.056  
127                   0.054  
415                   0.050  
375                   0.050  
335                   0.048  
216                   0.044  
235                   0.036  
43                    0.034  
49                    0.026  
264                   0.026

In [15]:
print('MIDFIELDERS')
display(my_df
        .drop(['team', 'expected_points_with_noise_with_decay'], axis=1)
        [my_df['position']=='MID']
        .sort_values(by='dream_team_appearances', ascending=False)
        .head(20))

MIDFIELDERS


name        team_name  expected_points  \
296           Mohamed Salah        Liverpool        63.611433   
61              Bukayo Saka          Arsenal        57.479137   
184            Jarrod Bowen         West Ham        52.990589   
149           Heung-Min Son        Tottenham        55.067800   
174          James Maddison        Tottenham        50.755953   
225            Kaoru Mitoma         Brighton        48.351994   
180       James Ward-Prowse         West Ham        46.111755   
58   Bruno Borges Fernandes   Manchester Utd        48.202344   
332             Pascal Groß         Brighton        46.968736   
60             Bryan Mbeumo        Brentford        46.722017   
338              Phil Foden  Manchester City        45.607776   
342         Raheem Sterling          Chelsea        45.267754   
270         Martin Ødegaard          Arsenal        46.405024   
266         Marcus Rashford   Manchester Utd        45.410200   
161           Jack Grealish  Manchester City        42.107202   
300            Moussa Diaby      Aston Villa        41.570520   
112            Eberechi Eze   Crystal Palace        40.764540   
379             Solly March         Brighton        41.956478   
273             Mason Mount   Manchester Utd        39.503344   
109      Dominik Szoboszlai        Liverpool        40.396660   

     expected_points_with_decay  number_of_games position  price  \
296                   16.566857               10      MID   12.5   
61                    15.130709               10      MID    8.7   
184                   14.188331               10      MID    7.1   
149                   14.578781               10      MID    9.2   
174                   13.431332               10      MID    7.9   
225                   12.557580               10      MID    6.6   
180                   12.259567               10      MID    6.3   
58                    12.864694               10      MID    8.4   
332                   12.130946               10      MID    6.3   
60                    12.255409               10      MID    6.9   
338                   12.163270               10      MID    7.6   
342                   12.170615               10      MID    7.1   
270                   12.196363               10      MID    8.5   
266                   12.168751               10      MID    8.9   
161                   11.279459               10      MID    7.3   
300                   11.120462               10      MID    6.6   
112                   10.711526               10      MID    6.3   
379                   10.833520               10      MID    6.6   
273                   10.610049               10      MID    6.9   
109                   10.447309               10      MID    7.0   

     dream_team_appearances  
296                   0.854  
61                    0.786  
184                   0.672  
149                   0.550  
174                   0.428  
225                   0.286  
180                   0.218  
58                    0.182  
332                   0.180  
60                    0.148  
338                   0.128  
342                   0.128  
270                   0.084  
266                   0.056  
161                   0.054  
300                   0.044  
112                   0.022  
379                   0.018  
273                   0.016  
109                   0.012

In [16]:
print('FORWARDS')
display(my_df
        .drop(['team', 'expected_points_with_noise_with_decay'], axis=1)
        [my_df['position']=='FWD']
        .sort_values(by='dream_team_appearances', ascending=False)
        .head(20))

FORWARDS


name          team_name  expected_points  \
218                    Julián Álvarez    Manchester City        46.779691   
325                     Ollie Watkins        Aston Villa        46.908045   
123                    Erling Haaland    Manchester City        55.146449   
64                      Callum Wilson      Newcastle Utd        44.534145   
70                     Carlton Morris              Luton        37.187828   
312                   Nicolas Jackson            Chelsea        40.697029   
108                   Dominic Solanke        Bournemouth        39.044600   
12                     Alexander Isak      Newcastle Utd        39.781901   
419                       Yoane Wissa          Brentford        37.846445   
96               Darwin Núñez Ribeiro          Liverpool        39.757886   
289                   Michail Antonio           West Ham        35.210947   
83                         Cody Gakpo          Liverpool        36.156005   
382                     Taiwo Awoniyi  Nottingham Forest        36.985385   
256                       Lyle Foster            Burnley        30.717426   
10                Aleksandar Mitrović             Fulham        30.811228   
125                     Evan Ferguson           Brighton        34.930804   
163                       Jacob Brown              Luton        23.193002   
94                      Danny Welbeck           Brighton        33.186939   
276  Matheus Santos Carneiro Da Cunha             Wolves        28.487781   
309                       Neal Maupay          Brentford        22.914509   

     expected_points_with_decay  number_of_games position  price  \
218                   12.458734               10      FWD    7.0   
325                   12.606532               10      FWD    7.9   
123                   14.709075               10      FWD   14.1   
64                    11.925205               10      FWD    7.8   
70                    10.735154               11      FWD    5.5   
312                   10.964179               10      FWD    6.9   
108                   10.356684               10      FWD    6.4   
12                    10.670216               10      FWD    7.6   
419                    9.978754               10      FWD    6.0   
96                    10.283567               10      FWD    7.4   
289                    9.382597               10      FWD    5.9   
83                     9.351280               10      FWD    7.3   
382                    9.684542               10      FWD    6.6   
256                    8.496215               11      FWD    5.0   
10                     8.126555               10      FWD    7.5   
125                    9.000539               10      FWD    6.0   
163                    6.671750               11      FWD    4.9   
94                     8.536560               10      FWD    5.8   
276                    7.356798               10      FWD    5.5   
309                    6.013512               10      FWD    4.9   

     dream_team_appearances  
218                   0.430  
325                   0.414  
123                   0.326  
64                    0.254  
70                    0.154  
312                   0.106  
108                   0.070  
12                    0.052  
419                   0.038  
96                    0.022  
289                   0.016  
83                    0.010  
382                   0.008  
256                   0.006  
10                    0.004  
125                   0.002  
163                   0.002  
94                    0.002  
276                   0.000  
309                   0.000

In [17]:
players = optimize(my_df, max_price, 'dream_team_appearances', captain_double_points=False)

Welcome to the CBC MILP Solver 
Version: 2.10.3 
Build Date: Dec 15 2019 

command line - /Users/jaakkotoivonen/Documents/my_stuff/Fantasy-Premier-League/venv23-24/lib/python3.10/site-packages/pulp/solverdir/cbc/osx/64/cbc /var/folders/ml/jr8p__z97xx1jjb90rwg7hfm0000gn/T/7cc6d596fd8e4aee849e22da09bb8423-pulp.mps max timeMode elapsed branch printingOptions all solution /var/folders/ml/jr8p__z97xx1jjb90rwg7hfm0000gn/T/7cc6d596fd8e4aee849e22da09bb8423-pulp.sol (default strategy 1)
At line 2 NAME          MODEL
At line 3 ROWS
At line 457 COLUMNS
At line 5448 RHS
At line 5901 BOUNDS
At line 6748 ENDATA
Problem MODEL has 452 rows, 846 columns and 3162 elements
Coin0008I MODEL read with 0 errors
Option for timeMode changed from cpu to elapsed
Continuous objective value is 5.71032 - 0.00 seconds
Cgl0004I processed model has 450 rows, 846 columns (846 integer (846 of which binary)) and 2961 elements
Cutoff increment increased from 1e-05 to 0.001998
Cbc0038I Initial state - 2 integers unsatisfie

position                    name             team  price  \
16        GK         Alphonse Areola         West Ham    4.2   
23       DEF        Andrew Robertson        Liverpool    6.6   
231      DEF         Kieran Trippier    Newcastle Utd    6.6   
282      DEF              Matty Cash      Aston Villa    4.8   
400      DEF  Trent Alexander-Arnold        Liverpool    7.9   
149      MID           Heung-Min Son        Tottenham    9.2   
174      MID          James Maddison        Tottenham    7.9   
184      MID            Jarrod Bowen         West Ham    7.1   
296      MID           Mohamed Salah        Liverpool   12.5   
61       MID             Bukayo Saka          Arsenal    8.7   
218      FWD          Julián Álvarez  Manchester City    7.0   

     dream_team_appearances  
16                    0.126  
23                    0.570  
231                   0.452  
282                   0.164  
400                   0.638  
149                   0.550  
174                   0.428  
184                   0.672  
296                   0.854  
61                    0.786  
218                   0.430

In [18]:
projections[(projections.gameweek==(latest_gameweek+1))].sort_values('expected_points', ascending=False)[['name', 'expected_points']].head(20)

name  expected_points
1859               Jarrod Bowen         6.656738
1243             Erling Haaland         6.103675
2304            Kevin De Bruyne         6.017808
616                 Bukayo Saka         5.797890
2991              Mohamed Salah         5.771183
1819          James Ward-Prowse         5.495334
3413                 Phil Foden         5.406609
2203             Julián Álvarez         5.368570
1504              Heung-Min Son         5.093922
1626              Jack Grealish         5.027988
3453            Raheem Sterling         5.025251
586      Bruno Borges Fernandes         5.016146
606                Bryan Mbeumo         4.989379
2729            Martin Ødegaard         4.941032
1152  Ederson Santana de Moraes         4.865705
2334            Kieran Trippier         4.785238
2689            Marcus Rashford         4.718917
646               Callum Wilson         4.653555
3656      Rúben Gato Alves Dias         4.628164
3152            Nicolas Jackson         4.614084

In [19]:
display(projections[projections.name.str.contains('Saliba')][['name', 'expected_points']])
display(projections[projections.name.str.contains('Saliba')][['expected_points_with_decay']].sum())

name  expected_points
4191  William Saliba         3.997678
4192  William Saliba         2.605301
4193  William Saliba         3.201558
4194  William Saliba         4.602218
4195  William Saliba         2.862416
4196  William Saliba         4.018905
4197  William Saliba         3.266904
4198  William Saliba         4.281946
4199  William Saliba         3.723326
4200  William Saliba         3.353782

expected_points_with_decay    9.41853
dtype: float64